In [41]:
import os
import cv2
import numpy as np
import matplotlib.pyplot as plt
from transformers import AutoFeatureExtractor, AutoModelForImageClassification, pipeline , ViTImageProcessor

In [1]:
# Open_slide fix

OPENSLIDE_PATH = r'C:\Users\DSAI\anaconda3\envs\tf\Lib\site-packages\openslide\openslide-win64-20231011\bin'

import os
if hasattr(os, 'add_dll_directory'):
    # Windows
    with os.add_dll_directory(OPENSLIDE_PATH):
        import openslide
else:
    import openslide

In [2]:
import openslide

In [3]:
from openslide import open_slide

In [4]:
slide = open_slide("inference_slide/tumor_065.tif")

In [5]:
slide_props = slide.properties
print(slide_props)

<_PropertyMap {'openslide.associated.macro.height': '1577', 'openslide.associated.macro.width': '3629', 'openslide.level-count': '10', 'openslide.level[0].downsample': '1', 'openslide.level[0].height': '220672', 'openslide.level[0].tile-height': '512', 'openslide.level[0].tile-width': '512', 'openslide.level[0].width': '97792', 'openslide.level[1].downsample': '2', 'openslide.level[1].height': '110336', 'openslide.level[1].tile-height': '512', 'openslide.level[1].tile-width': '512', 'openslide.level[1].width': '48896', 'openslide.level[2].downsample': '4', 'openslide.level[2].height': '55168', 'openslide.level[2].tile-height': '512', 'openslide.level[2].tile-width': '512', 'openslide.level[2].width': '24448', 'openslide.level[3].downsample': '8', 'openslide.level[3].height': '27584', 'openslide.level[3].tile-height': '512', 'openslide.level[3].tile-width': '512', 'openslide.level[3].width': '12224', 'openslide.level[4].downsample': '16', 'openslide.level[4].height': '13792', 'openslide

In [6]:
print("Vendor is:", slide_props['openslide.vendor'])
print("Pixel size of X in um is:", slide_props['openslide.mpp-x'])
print("Pixel size of Y in um is:", slide_props['openslide.mpp-y'])

Vendor is: philips
Pixel size of X in um is: 0.24309399999999998
Pixel size of Y in um is: 0.24309399999999998


In [7]:
slide_dims = slide.dimensions
print(slide_dims)

(97792, 220672)


In [8]:
slide_thumb_600 = slide.get_thumbnail(size=(1000,1000))
slide_thumb_600.show()

In [13]:
dims = slide.level_dimensions

In [14]:
dims

((97792, 220672),
 (48896, 110336),
 (24448, 55168),
 (12224, 27584),
 (6112, 13792),
 (3056, 6896),
 (1528, 3448),
 (764, 1724),
 (382, 862),
 (191, 431))

In [18]:
level3_dim = dims[7]

In [19]:
level3_dim

(764, 1724)

In [20]:
#Give pixel coordinates (top left pixel in the original large image)
#Also give the level number (for level 3 we are providing a valueof 2)
#Size of your output image
#Remember that the output would be a RGBA image (Not, RGB)
level3_img = slide.read_region((0,0), 2, level3_dim) #Pillow object, mode=RGBA

#Convert the image to RGB
level3_img_RGB = level3_img.convert('RGB')
level3_img_RGB.show()

In [21]:
from openslide.deepzoom import DeepZoomGenerator

In [22]:
tiles = DeepZoomGenerator(slide, tile_size=256, overlap=0, limit_bounds=False)

In [23]:
print("The number of levels in the tiles object are: ", tiles.level_count)

print("The dimensions of data in each level are: ", tiles.level_dimensions)

The number of levels in the tiles object are:  19
The dimensions of data in each level are:  ((1, 1), (1, 2), (2, 4), (3, 7), (6, 14), (12, 27), (24, 54), (48, 108), (96, 216), (191, 431), (382, 862), (764, 1724), (1528, 3448), (3056, 6896), (6112, 13792), (12224, 27584), (24448, 55168), (48896, 110336), (97792, 220672))


In [24]:
print("Total number of tiles = : ", tiles.tile_count)

Total number of tiles = :  439269


---------level 0------------ 

In [35]:
level_num = 18
print("Tiles shape at level ", level_num, " is: ", tiles.level_tiles[level_num])
print("This means there are ", tiles.level_tiles[level_num][0]*tiles.level_tiles[level_num][1], " total tiles in this level")

Tiles shape at level  18  is:  (382, 862)
This means there are  329284  total tiles in this level


In [38]:
cols, rows = tiles.level_tiles[18]

In [39]:
cols , rows

(382, 862)

In [44]:
import os
tile_dir = "WSI/tiles/"
for row in range(rows):
    for col in range(cols):
        tile_name = os.path.join(tile_dir, '%d_%d' % (col, row))
        print("Now saving tile with title: ", tile_name)
        temp_tile = tiles.get_tile(18, (col, row))
        temp_tile_RGB = temp_tile.convert('RGB')
        temp_tile_np = np.array(temp_tile_RGB)
        plt.imsave(tile_name + ".png", temp_tile_np)

Now saving tile with title:  WSI/tiles/0_0
Now saving tile with title:  WSI/tiles/1_0
Now saving tile with title:  WSI/tiles/2_0
Now saving tile with title:  WSI/tiles/3_0
Now saving tile with title:  WSI/tiles/4_0
Now saving tile with title:  WSI/tiles/5_0
Now saving tile with title:  WSI/tiles/6_0
Now saving tile with title:  WSI/tiles/7_0
Now saving tile with title:  WSI/tiles/8_0
Now saving tile with title:  WSI/tiles/9_0
Now saving tile with title:  WSI/tiles/10_0
Now saving tile with title:  WSI/tiles/11_0
Now saving tile with title:  WSI/tiles/12_0
Now saving tile with title:  WSI/tiles/13_0
Now saving tile with title:  WSI/tiles/14_0
Now saving tile with title:  WSI/tiles/15_0
Now saving tile with title:  WSI/tiles/16_0
Now saving tile with title:  WSI/tiles/17_0
Now saving tile with title:  WSI/tiles/18_0
Now saving tile with title:  WSI/tiles/19_0
Now saving tile with title:  WSI/tiles/20_0
Now saving tile with title:  WSI/tiles/21_0
Now saving tile with title:  WSI/tiles/22_

In [ ]:
feature_extractor = ViTImageProcessor.from_pretrained("anurag2op/vit-large-patch16-224-in21k-finetuned-pcam")
model = AutoModelForImageClassification.from_pretrained("anurag2op/vit-large-patch16-224-in21k-finetuned-pcam")

In [ ]:
model

In [ ]:
pipe = pipeline("image-classification", model=model, feature_extractor=feature_extractor)

In [ ]:
PATH = 'WSI/tiles/'

In [ ]:
image = cv2.imread(os.path.join(PATH + '126_558.png'))

plt.imshow(image)

In [ ]:
results = pipe(os.path.join(PATH + '126_558.png'))

In [ ]:
results[0]['label']

In [ ]:
overlay = np.full_like(image, (255,0,0), dtype=np.uint8)  
image_n = cv2.addWeighted(overlay, 0.4, image, 0.8, 0)

In [ ]:
plt.imshow(image_n) 

In [ ]:
plt.imshow(image)